In [ ]:
#general purpose packages
import numpy as np
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
import seaborn as sns

#data processing
import nltk
import re, string
!pip install emoji
import emoji
from collections import Counter


from sklearn import preprocessing
from imblearn.over_sampling import RandomOverSampler
from sklearn.model_selection import train_test_split


#Naive Bayes
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.naive_bayes import MultinomialNB

#transformers
!pip install transformers
from transformers import BertTokenizerFast
from transformers import TFBertModel
from transformers import RobertaTokenizerFast
from transformers import TFRobertaModel

#keras
import tensorflow as tf
from tensorflow import keras


#metrics
from sklearn.metrics import accuracy_score, f1_score
from sklearn.metrics import classification_report, confusion_matrix

#set seed for reproducibility
seed=42

#set style for plots
sns.set_style("whitegrid")
sns.despine()
plt.style.use("seaborn-whitegrid")
plt.rc("figure", autolayout=True)
plt.rc("axes", labelweight="bold", labelsize="large", titleweight="bold", titlepad=10)

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 358.9/358.9 kB 5.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 44.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 26.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 91.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 77.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 30.7 MB/s eta 0:00:00


<ipython-input-1-c615114577cc>:48: MatplotlibDeprecationWarning: The seaborn styles shipped by Matplotlib are deprecated since 3.6, as they no longer correspond to the styles shipped by seaborn. However, they will remain available as 'seaborn-v0_8-<style>'. Alternatively, directly use the seaborn API instead.
  plt.style.use("seaborn-whitegrid")


<Figure size 640x480 with 0 Axes>

In [ ]:
##CUSTOM DEFINED FUNCTIONS TO CLEAN THE TWEETS


#Remove punctuations, links, mentions and \r\n new line characters
def strip_all_entities(text):
    text = text.replace('\r', '').replace('\n', ' ').replace('\n', ' ').lower() #remove \n and \r and lowercase
    text = re.sub(r"(?:\@|https?\://)\S+", "", text) #remove links and mentions
    text = re.sub(r'[^\x00-\x7f]',r'', text) #remove non utf8/ascii characters such as '\x9a\x91\x97\x9a\x97'
    banned_list= string.punctuation + 'Ã'+'±'+'ã'+'¼'+'â'+'»'+'§'
    table = str.maketrans('', '', banned_list)
    text = text.translate(table)
    return text

#clean hashtags at the end of the sentence, and keep those in the middle of the sentence by removing just the # symbol
def clean_hashtags(tweet):
    new_tweet = " ".join(word.strip() for word in re.split('#(?!(?:hashtag)\b)[\w-]+(?=(?:\s+#[\w-]+)*\s*$)', tweet)) #remove last hashtags
    new_tweet2 = " ".join(word.strip() for word in re.split('#|_', new_tweet)) #remove hashtags symbol from words in the middle of the sentence
    return new_tweet2

#Filter special characters such as & and $ present in some words
def filter_chars(a):
    sent = []
    for word in a.split(' '):
        if ('$' in word) | ('&' in word):
            sent.append('')
        else:
            sent.append(word)
    return ' '.join(sent)

def remove_mult_spaces(text): # remove multiple spaces
    return re.sub("\s\s+" , " ", text)

In [ ]:
Amazon = pd.read_csv('/content/drive/Othercomputers/Laptop/2023 Spring 2/COMPSCI 760/Electronics_5.csv')
Amazon['reviewText'] = Amazon['reviewText'].astype(str)
Amazon['summary'] = Amazon['summary'].astype(str)
Amazon['reviews_text'] = Amazon['summary'] + ' ' + Amazon['reviewText']
Amazon['id'] = Amazon['reviewerID']
Amazon['reviews_username'] = Amazon['reviewerID']
Amazon['name'] = Amazon['asin']
Amazon.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50000 entries, 0 to 49999
Data columns (total 11 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   overall           50000 non-null  int64 
 1   reviewerID        50000 non-null  object
 2   asin              50000 non-null  object
 3   reviewerName      49996 non-null  object
 4   reviewText        50000 non-null  object
 5   summary           50000 non-null  object
 6   user_sentiment    50000 non-null  object
 7   reviews_text      50000 non-null  object
 8   id                50000 non-null  object
 9   reviews_username  50000 non-null  object
 10  name              50000 non-null  object
dtypes: int64(1), object(10)
memory usage: 4.2+ MB


In [ ]:
first_row = Amazon.iloc[0]
print(first_row)

overall                                                             5
reviewerID                                             A3PODFMWAGFM84
asin                                                       B014MZVI86
reviewerName                                              aponyo flip
reviewText          These are great.  I had another pair similar b...
summary             Great for camping and getting (close) to objects.
user_sentiment                                               Positive
reviews_text        Great for camping and getting (close) to objec...
id                                                     A3PODFMWAGFM84
reviews_username                                       A3PODFMWAGFM84
name                                                       B014MZVI86
Name: 0, dtype: object


In [ ]:
Amazon = Amazon[['reviews_text','user_sentiment','id']]
df, df_test = train_test_split(Amazon[0:50000], test_size=0.8, random_state=63)
df.to_csv("train.csv",index=False)
df.shape

(10000, 3)

In [ ]:
df_test.to_csv("test.csv",index=False)
df_test.shape

(40000, 3)

In [ ]:
df.drop_duplicates(subset='reviews_text',inplace=True)

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9704 entries, 48839 to 5164
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   reviews_text    9704 non-null   object
 1   user_sentiment  9704 non-null   object
 2   id              9704 non-null   object
dtypes: object(3)
memory usage: 303.2+ KB


In [ ]:
texts_new = []
for t in df.reviews_text:
    texts_new.append(remove_mult_spaces(filter_chars(clean_hashtags(strip_all_entities(t)))))

In [ ]:
texts_new_test = []
for t in df_test.reviews_text:
    texts_new_test.append(remove_mult_spaces(filter_chars(clean_hashtags(strip_all_entities(t)))))

In [ ]:
df['text_clean'] = texts_new
df_test['text_clean'] = texts_new_test

In [ ]:
df['text_clean'].head()

48839    i guess you get what you pay for i ordered two...
10330    you cant go wrong with this hard drive i bough...
49303    awesome color very happy with this purchase go...
6892     works this worked perfectly right out of the b...
17957    didnt work poor quality complicated and when y...
Name: text_clean, dtype: object

In [ ]:
df_test['text_clean'].head()

9700     good replacement for oem wish i hadnt lost the...
21894                                 four stars very good
10062    jury is out system doesnt recognize portable h...
10123    great little keyboard for htpc or smart tv wit...
15647    im anal the wife is particular were both extre...
Name: text_clean, dtype: object

In [ ]:
df['text_clean'][1:8].values

array(['you cant go wrong with this hard drive i bought a 1tb version as a secondary drive that i keep pictures documents and other misc files on its high quality and has worked flawlessly so far in the past 2 years',
       'awesome color very happy with this purchase got this color specifically to stand out from the usual colors i have seen people are constantly asking me where i got it strap is same color as camera but with white polka dots extremely happy with purchase also buy your film on amazon you get more prints for less money vs buying at target or walmart',
       'works this worked perfectly right out of the box didnt have to configure anything to use my old pantech um175 just plugged it in and it worked fine',
       'didnt work poor quality complicated and when your finished with trying to get it to do something you may as well have left it in the package',
       'one star terrible product does not stick to my 2012 honda pilot dashboard beware',
       'five stars perfec

In [ ]:
text_len = []
for text in df.text_clean:
    tweet_len = len(text.split())
    text_len.append(tweet_len)

In [ ]:
df['text_len'] = text_len

In [ ]:
text_len_test = []
for text in df_test.text_clean:
    tweet_len = len(text.split())
    text_len_test.append(tweet_len)

In [ ]:
df_test['text_len'] = text_len_test

In [ ]:
df = df[df['text_len'] > 4]
df_test = df_test[df_test['text_len'] > 4]
print(f" DF SHAPE: {df.shape}")
print(f" DF TEST SHAPE: {df_test.shape}")

 DF SHAPE: (9179, 5)
 DF TEST SHAPE: (36747, 5)


In [ ]:
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')

In [ ]:
token_lens = []

for txt in df['text_clean'].values:
    tokens = tokenizer.encode(txt, max_length=512, truncation=True)
    token_lens.append(len(tokens))

max_len=np.max(token_lens)

In [ ]:
print(f"MAX TOKENIZED SENTENCE LENGTH: {max_len}")

MAX TOKENIZED SENTENCE LENGTH: 512


In [ ]:
token_lens = []

for i,txt in enumerate(df['text_clean'].values):
    tokens = tokenizer.encode(txt, max_length=512, truncation=True)
    token_lens.append(len(tokens))
    if len(tokens)>80:
        print(f"INDEX: {i}, TEXT: {txt}")

INDEX: 11, TEXT: great piece of equipment great piece of equipment tons of options and different kinds of plugins on the back very strong volume for a unit of this size nice equalizer slider buttons on the back bluetooth works great mics work well but yes you do need them to be right on your lips for the best sound not a big deal for me as i use it to speak and not perform as a singer a singer will probably want to use their own directional mic and plug it in to the back where there are extra audioin plugs i used it at a recent event and it was a huge hit worked very well love that it has a builtin battery for situations where you have no electricity i would use good 9v batteries though if you use cheap ones your wireless mic power will dwindle down after a while depending on how you use it the unit doesnt weigh a ton either its light enough to lug in and out of your car fairly easily
INDEX: 18, TEXT: does not include full height bracket great customer service i purchased this card not

In [ ]:
df['token_lens'] = token_lens

In [ ]:
df = df.sort_values(by='token_lens', ascending=False)
df.head(20)

reviews_text user_sentiment  \
16259  Very capable closed cans "Senns," as they are ...       Positive   
19773  Great PC After Changes I had been debating bet...       Positive   
30400  Super fast SSD for a great price I have been u...       Positive   
11416  Versatile performer, but overpriced compared t...       Negative   
21024  Good entry level DSLR, but entry level is the ...       Negative   
22315  A worthy successor to the acclaimed WRT54G... ...       Positive   
1849   Out of the Box Functional and Working as Expec...       Positive   
29355  Asus 1000ha vs Asus 1000he I have the Asus 100...       Positive   
43365  Great audio quality in an environment-proof fo...       Positive   
20233  DO NOT GO WITH THIS PRODUCT. GAMERS AND CASUAL...       Negative   
48874  Best dap you've never heard of, feature king.....       Positive   
33087  Worked perfectly on an international trip to C...       Positive   
1990   Somewhat disappointed but can't beat the value...       Negative   
35767  Worthy Successor to A1000IS This camera is a w...       Positive   
32818  Installs Easily, Great Price, Fast Data Speed,...       Positive   
48607  The promise of open and easy access to all of ...       Positive   
38074  Crystal clear, tinny music & static on mic Phy...       Negative   
11511  When it works... it's great!!! I have problem ...       Negative   
46641  Not bad but I can't recommend it... I've had t...       Negative   
35125  Great seller, good for the money but mine brok...       Negative   

                   id                                         text_clean  \
16259   APBA7Y4SINS0H  very capable closed cans senns as they are cal...   
19773   A5UA6U7E1K8AG  great pc after changes i had been debating bet...   
30400   AC4TQ8K03VU7C  super fast ssd for a great price i have been u...   
11416  A3JZ5L52FM318H  versatile performer but overpriced compared to...   
21024  A35HNL2VEDK9Z1  good entry level dslr but entry level is the k...   
22315   A5YWF3BZZYR95  a worthy successor to the acclaimed wrt54g i w...   
1849   A1KL1YVYYMQE2E  out of the box functional and working as expec...   
29355  A2NUBL2UYWPBWR  asus 1000ha vs asus 1000he i have the asus 100...   
43365  A3J3ZHGDUDPCFL  great audio quality in an environmentproof for...   
20233  A325X0LGJZSISL  do not go with this product gamers and casual ...   
48874  A1IILFFC2EUXFC  best dap youve never heard of feature king i b...   
33087   A7M7JDSCN0HMM  worked perfectly on an international trip to c...   
1990     AJSNJRO2PA1J  somewhat disappointed but cant beat the value ...   
35767  A2OKRGHIYTBQ6P  worthy successor to a1000is this camera is a w...   
32818  A3V79KXIY09MOE  installs easily great price fast data speed wh...   
48607  A1VKAY0XWLA2CY  the promise of open and easy access to all of ...   
38074   AQF3D0KX5SFCM  crystal clear tinny music static on mic physic...   
11511  A1C79GZWPXKXW7  when it works its great i have problem with lg...   
46641  A2KDRLWOIHBHPR  not bad but i cant recommend it ive had this s...   
35125   AC63Q30CYESLK  great seller good for the money but mine broke...   

       text_len  token_lens  
16259       607         512  
19773      1052         512  
30400       763         512  
11416      1479         512  
21024       507         512  
22315       814         512  
1849        510         512  
29355       502         512  
43365       821         512  
20233       851         512  
48874       835         512  
33087       499         512  
1990       1121         512  
35767       490         512  
32818       653         512  
48607      1080         512  
38074       580         512  
11511       478         512  
46641       564         512  
35125       708         512

In [ ]:
df = df.iloc[12:]
df.head()

reviews_text user_sentiment  \
1990   Somewhat disappointed but can't beat the value...       Negative   
35767  Worthy Successor to A1000IS This camera is a w...       Positive   
32818  Installs Easily, Great Price, Fast Data Speed,...       Positive   
48607  The promise of open and easy access to all of ...       Positive   
38074  Crystal clear, tinny music & static on mic Phy...       Negative   

                   id                                         text_clean  \
1990     AJSNJRO2PA1J  somewhat disappointed but cant beat the value ...   
35767  A2OKRGHIYTBQ6P  worthy successor to a1000is this camera is a w...   
32818  A3V79KXIY09MOE  installs easily great price fast data speed wh...   
48607  A1VKAY0XWLA2CY  the promise of open and easy access to all of ...   
38074   AQF3D0KX5SFCM  crystal clear tinny music static on mic physic...   

       text_len  token_lens  
1990       1121         512  
35767       490         512  
32818       653         512  
48607      1080         512  
38074       580         512

In [ ]:
df = df.sample(frac=1).reset_index(drop=True)

In [ ]:
token_lens_test = []

for txt in df_test['text_clean'].values:
    tokens = tokenizer.encode(txt, max_length=512, truncation=True)
    token_lens_test.append(len(tokens))

max_len=np.max(token_lens_test)

In [ ]:
print(f"MAX TOKENIZED SENTENCE LENGTH: {max_len}")

MAX TOKENIZED SENTENCE LENGTH: 512


In [ ]:
token_lens_test = []

for i,txt in enumerate(df_test['text_clean'].values):
    tokens = tokenizer.encode(txt, max_length=512, truncation=True)
    token_lens_test.append(len(tokens))
    if len(tokens)>80:
        print(f"INDEX: {i}, TEXT: {txt}")

流式输出内容被截断，只能显示最后 5000 行内容。
INDEX: 19756, TEXT: even better than exptected i have set up and installed many security cameras by the big names but i was trying to do a job on the cheap and saw these cameras with some pretty stellar ability on paper i figured i could not go wrong given the low price i was incredibly surprised to find that not only are they really good cameras that were easy to set up and install they are actually better than most others i have used that come in at double the price i will definitely be looking to reolink for many more jobs going forward
INDEX: 19757, TEXT: standard performance i wasnt wowed at all i guess somewhat disappointed in thinking i was getting a deal in a performance speaker and just found myself liking the design more than anything i am well familiar with speakers be it that i have studied and designed some custom enclosures in mfd glass etc knowing ohms and proper wattage crossovers and acoustic fillers dampening and blah blah blah i enjoy all k

In [ ]:
df_test['token_lens'] = token_lens_test
df_test = df_test.sort_values(by='token_lens', ascending=False)
df_test.head(10)
df_test = df_test.iloc[5:]
df_test.head(3)

reviews_text user_sentiment  \
15762  Great Headset for Sound, but Watch Out for Acc...       Negative   
13072  solid router -The user interface is excellent ...       Positive   
25103  Don't believe the hype. I am a long-time user ...       Negative   

                   id                                         text_clean  \
15762   ALBD3P1D8H1JI  great headset for sound but watch out for acci...   
13072  A1RK5HLK1JGUK8  solid router the user interface is excellent a...   
25103  A2IJF9E51O7QLX  dont believe the hype i am a longtime user of ...   

       text_len  token_lens  
15762       674         512  
13072       501         512  
25103       537         512

In [ ]:
df_test = df_test.sample(frac=1).reset_index(drop=True)

In [ ]:
df.to_csv("trainclean.csv")
df_test.to_csv("testclean.csv")

In [ ]:
df['user_sentiment'].unique()
df = df.dropna(subset=['user_sentiment']).copy()

In [ ]:
df_test['user_sentiment'].unique()
df_test = df_test.dropna(subset=['user_sentiment']).copy()

In [ ]:
df['user_sentiment'].value_counts()
df['user_sentiment'].unique()
df['user_sentiment'] = df['user_sentiment'].map({'Negative':0,'Positive':1})
df_test['user_sentiment'] = df_test['user_sentiment'].map({'Negative':0,'Positive':1})
df['user_sentiment'].value_counts()

1    7296
0    1871
Name: user_sentiment, dtype: int64

In [ ]:
df['user_sentiment'].unique()

array([1, 0])

In [ ]:
df_test['user_sentiment'].unique()

array([1, 0])

In [ ]:
ros = RandomOverSampler()
train_x, train_y = ros.fit_resample(np.array(df['text_clean']).reshape(-1, 1), np.array(df['user_sentiment']).reshape(-1, 1));
train_os = pd.DataFrame(list(zip([x[0] for x in train_x], train_y)), columns = ['text_clean', 'user_sentiment']);
train_os['user_sentiment'].value_counts()

1    7296
0    7296
Name: user_sentiment, dtype: int64

In [ ]:
X = train_os['text_clean'].values
y = train_os['user_sentiment'].values

In [ ]:
X_train, X_valid, y_train, y_valid= train_test_split(X, y ,test_size=0.5, stratify=y, random_state=seed)
ID_test = df_test['id'].values
Text_test = df_test['reviews_text'].values
X_test = df_test['text_clean'].values
y_test = df_test['user_sentiment'].values

In [ ]:
y_train_le = y_train.copy()
y_valid_le = y_valid.copy()
y_test_le = y_test.copy()
ohe = preprocessing.OneHotEncoder()
y_train = ohe.fit_transform(np.array(y_train).reshape(-1, 1)).toarray()
y_valid = ohe.fit_transform(np.array(y_valid).reshape(-1, 1)).toarray()
y_test = ohe.fit_transform(np.array(y_test).reshape(-1, 1)).toarray()
print(f"TRAINING DATA: {X_train.shape[0]}\nVALIDATION DATA: {X_valid.shape[0]}\nTESTING DATA: {X_test.shape[0]}" )

TRAINING DATA: 7296
VALIDATION DATA: 7296
TESTING DATA: 36742


In [ ]:
tokenizer_roberta = RobertaTokenizerFast.from_pretrained("roberta-base")
token_lens = []

for txt in X_train:
    tokens = tokenizer_roberta.encode(txt, max_length=512, truncation=True)
    token_lens.append(len(tokens))
for txt in X_test:
    tokens = tokenizer_roberta.encode(txt, max_length=512, truncation=True)
    token_lens.append(len(tokens))
max_length=np.max(token_lens)
max_length

512

In [ ]:
MAX_LEN=512

In [ ]:
def tokenize_roberta(data, max_len=MAX_LEN):
    input_ids = []
    attention_masks = []

    for i in range(len(data)):
        # Encoding text using a tokenizer
        encoded = tokenizer_roberta.encode_plus(
            data[i],
            add_special_tokens=True,
            max_length=max_len,
            padding='max_length',
            return_attention_mask=True
        )

        # Truncate or fill input_ids and attention_masks to the same length.
        input_id = encoded['input_ids'][:max_len]
        attention_mask = encoded['attention_mask'][:max_len]

        input_ids.append(input_id)
        attention_masks.append(attention_mask)

    # Convert lists to NumPy arrays, making sure they have the same length
    input_ids_array = np.array(input_ids)
    attention_masks_array = np.array(attention_masks)

    return input_ids_array, attention_masks_array

In [ ]:
MAX_LEN

512

In [ ]:
train_input_ids, train_attention_masks = tokenize_roberta(X_train, MAX_LEN)
val_input_ids, val_attention_masks = tokenize_roberta(X_valid, MAX_LEN)
test_input_ids, test_attention_masks = tokenize_roberta(X_test, MAX_LEN)

In [ ]:
Counter(len(arr) for arr in train_input_ids)

Counter({512: 7296})

In [ ]:
Counter(len(arr) for arr in val_input_ids)


Counter({512: 7296})

In [ ]:
Counter(len(arr) for arr in test_input_ids)


Counter({512: 36742})

In [ ]:
Counter(len(arr) for arr in train_attention_masks)


Counter({512: 7296})

In [ ]:
Counter(len(arr) for arr in val_attention_masks)


Counter({512: 7296})

In [ ]:
Counter(len(arr) for arr in test_attention_masks)

Counter({512: 36742})

In [ ]:
len(ID_test)

36742

Check the test data index

In [ ]:
df_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36742 entries, 0 to 36741
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   reviews_text    36742 non-null  object
 1   user_sentiment  36742 non-null  int64 
 2   id              36742 non-null  object
 3   text_clean      36742 non-null  object
 4   text_len        36742 non-null  int64 
 5   token_lens      36742 non-null  int64 
dtypes: int64(3), object(3)
memory usage: 1.7+ MB


In [ ]:
acc=accuracy_score(X_test,df_test.loc[df_test['id'].isin(ID_test), 'text_clean'])
print(f'Accuracy:{acc}')

Accuracy:1.0


In [ ]:
def create_model(bert_model, max_len=MAX_LEN):
    initial_learning_rate = 1e-5
    decay_steps = 1000
    decay_rate = 0.9

    # Creating Learning Rate Decay Strategies
    learning_rate_schedule = tf.keras.optimizers.schedules.ExponentialDecay(
        initial_learning_rate, decay_steps, decay_rate)

    # Creating an optimiser using a learning rate strategy
    opt = tf.keras.optimizers.Adam(learning_rate=learning_rate_schedule)
    loss = tf.keras.losses.CategoricalCrossentropy()
    accuracy = tf.keras.metrics.CategoricalAccuracy()

    input_ids = tf.keras.Input(shape=(max_len,),dtype='int32')
    attention_masks = tf.keras.Input(shape=(max_len,),dtype='int32')
    output = bert_model([input_ids,attention_masks])
    output = output[1]
    output = tf.keras.layers.Dense(2, activation=tf.nn.softmax)(output)
    model = tf.keras.models.Model(inputs = [input_ids,attention_masks],outputs = output)
    model.compile(opt, loss=loss, metrics=accuracy)
    return model
roberta_model = TFRobertaModel.from_pretrained('roberta-base')

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFRobertaModel: ['lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.bias', 'lm_head.layer_norm.weight', 'roberta.embeddings.position_ids']
- This IS expected if you are initializing TFRobertaModel from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFRobertaModel from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
Some weights or buffers of the TF 2.0 model TFRobertaModel were not initialized from the PyTorch model and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and infe

In [ ]:
model = create_model(roberta_model, MAX_LEN)
model.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 512)]                0         []                            
                                                                                                  
 input_2 (InputLayer)        [(None, 512)]                0         []                            
                                                                                                  
 tf_roberta_model (TFRobert  TFBaseModelOutputWithPooli   1246456   ['input_1[0][0]',             
 aModel)                     ngAndCrossAttentions(last_   32         'input_2[0][0]']             
                             hidden_state=(None, 512, 7                                           
                             68),                                                             

In [ ]:
history_2 = model.fit([train_input_ids,train_attention_masks], y_train, validation_data=([val_input_ids,val_attention_masks], y_valid), epochs=4, batch_size=32)

Epoch 1/4
228/228 [==============================] - 17580s 77s/step - loss: 0.3248 - categorical_accuracy: 0.8512 - val_loss: 0.1903 - val_categorical_accuracy: 0.9315
Epoch 2/4
228/228 [==============================] - 17651s 77s/step - loss: 0.1475 - categorical_accuracy: 0.9467 - val_loss: 0.1377 - val_categorical_accuracy: 0.9548
Epoch 3/4
228/228 [==============================] - 17718s 78s/step - loss: 0.0776 - categorical_accuracy: 0.9734 - val_loss: 0.1280 - val_categorical_accuracy: 0.9598
Epoch 4/4
228/228 [==============================] - 17725s 78s/step - loss: 0.0419 - categorical_accuracy: 0.9856 - val_loss: 0.1960 - val_categorical_accuracy: 0.9563


In [ ]:
result_roberta = model.predict([test_input_ids,test_attention_masks])
y_pred_roberta =  np.zeros_like(result_roberta)
y_pred_roberta[np.arange(len(y_pred_roberta)), result_roberta.argmax(1)] = 1

NameError: ignored

In [ ]:
print('\tClassification Report for RoBERTa:\n\n',classification_report(y_test,y_pred_roberta, target_names=['Negative', 'Positive']))

In [ ]:
from sklearn.metrics import accuracy_score
acc=accuracy_score(y_test,y_pred_roberta)
print(f'Accuracy:{acc}')

In [ ]:
Y_pred_roberta = np.argmax(y_pred_roberta, axis=1)
result_roberta = pd.DataFrame(columns=["id","Y_pred_roberta"])
result_roberta['id'] = ID_test
result_roberta['Y_pred_roberta'] = Y_pred_roberta
result_roberta['reviews_text'] = Text_test
result_roberta.to_csv('result.csv',index=False)

In [ ]:
from sklearn.metrics import f1_score, precision_score, recall_score, confusion_matrix


# calculate the confusion matrix
confusion = confusion_matrix(np.argmax(y_test, axis=1),np.argmax(y_pred_roberta, axis=1))

# calculate the F1score、recall and precision
precision = precision_score(np.argmax(y_test, axis=1),np.argmax(y_pred_roberta, axis=1))
recall = recall_score(np.argmax(y_test, axis=1),np.argmax(y_pred_roberta, axis=1))
f1 = f1_score(np.argmax(y_test, axis=1),np.argmax(y_pred_roberta, axis=1))

print("Precision:", precision,"\nRecall:", recall,"F1 Score:", f1)